# Partitioned Circuit Extraction Walkthrough

Final phase of the circuit partioning framework is the extraction of a partitioned quanutm circuit. 

Using the QuantumCircuitHyperGraph object and a node assignment function, we can infer the required teleportation operations and build a quantum cirucit.
The qubits are split across multiple registers - one for each partition. Each partition is also initialised with a communication qubit register and a classical bit register for facilitating the teleportation. Additional communication qubits may be added if there are not enough available.

## Build initial circuit

First build/import and transpile the circuit. We use a fixed depth random circuit as an example.

In [15]:
from disqco.circuits.cp_fraction import cp_fraction
from disqco.circuits.QAOA import QAOA_random
from disqco.graphs.GCP_hypergraph import QuantumCircuitHyperGraph
from qiskit import transpile
from disqco.parti.FM.FM_methods import set_initial_partitions
from qiskit.circuit.library import QFT, QuantumVolume, EfficientSU2
from disqco.utils.qiskit_to_op_list import *
from qiskit import QuantumCircuit
import numpy as np

num_qubits = 32

seed= np.random.randint(0,1000000)

# circuit = cp_fraction(  num_qubits = num_qubits,
#                         depth = 500,
#                         fraction= 0.5,
#                         seed=seed)

# circuit = QuantumVolume(num_qubits, 30, seed= seed)
circuit = QAOA_random(num_qubits, prob=0.5, reps=1)

num_qubits = circuit.num_qubits

circuit = transpile(circuit, basis_gates=['u', 'cp'])
depth = circuit.depth()

print(seed)


544645


## Graph building

We then build the graph using the QuantumCircuitHyperGraph object. We also define the paremeteres of the QPU architecture using the qpu_info and comm_info variables, which tell us how many physical qubits are in each partition.

We can draw the resulting graph using matplotlib. 

In [16]:

num_partitions = 4
qpu_size = int(num_qubits / num_partitions)
qpu_info = [qpu_size] * num_partitions

qpu_info[-1] += 1
comm_info = [1] * num_partitions

group_gates = True

graph = QuantumCircuitHyperGraph(circuit = circuit,
                                 group_gates = group_gates,
                                 anti_diag = True)


from disqco.graphs.quantum_network import QuantumNetwork

qnet = QuantumNetwork(qpu_info)

assignment = set_initial_partitions(network = qnet, 
                                    num_qubits = num_qubits, 
                                    depth = depth)

from disqco.parti.FM.FM_methods import calculate_full_cost

cost = calculate_full_cost(graph, assignment, num_partitions)

print("E-bit cost for unoptimised assignment: ", cost)


Number of layers: 159
E-bit cost for unoptimised assignment:  48


In [17]:
from disqco.drawing.tikz_drawing import *
from disqco.drawing.mpl_drawing import *
%load_ext jupyter_tikz

# if num_qubits <= 32:
#     fig = draw_graph_tikz(H=graph,assignment=assignment,qpu_info=qpu_info)

#     display(fig)


The jupyter_tikz extension is already loaded. To reload it, use:
  %reload_ext jupyter_tikz


## Naive extraction

We can first set a baseline for the distributed circuit by extracting a partitioned circuit directly from the unoptimised assignment function. This will likely result in a very deep circuit which does not use entanglement efficiently.

First import the extractor class, passing in the graph and the partition assignment that we initialised before.

In [18]:
from disqco.circuit_extraction.circuit_extractor_new import PartitionedCircuitExtractor



extractor = PartitionedCircuitExtractor(graph=graph, 
                                         partition_assignment=assignment, 
                                         qpu_info=qpu_info, 
                                         comm_info=comm_info)



basic_partitioned_circuit = extractor.extract_partitioned_circuit()

basic_partitioned_circuit_EPR = transpile(basic_partitioned_circuit, basis_gates=['cp','u','EPR'])

print(f"Depth of partitioned circuit: {basic_partitioned_circuit.depth()}")

EPR_count = basic_partitioned_circuit_EPR.count_ops()['EPR']
print(f"EPR count in partitioned circuit: {EPR_count}")



Processing layer 0
Processing layer 1
Processing group gate {'type': 'group', 'root': 0, 'time': 1, 'sub-gates': [{'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 5], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 1}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 5], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 3}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 6], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 4}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 6], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 6}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 7], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 7}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 7], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 9}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 8], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 10}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 8], 'qregs': ['q'

We can draw the circuit to see where the teleportation blocks are occurring.

In [19]:
if num_qubits < 12:
    fig = basic_partitioned_circuit.draw(output='mpl', style='bw', fold=100)
    fig.show()


To compare with original, we can transpile back into the U, CP gate-set, while choosing not to decompose the elementary entanglement generation options.

In [20]:
decomposed_circuit = transpile(basic_partitioned_circuit, basis_gates = ['cp', 'u', 'EPR'])

print(f"Depth of decomposed partitioned circuit: {decomposed_circuit.depth()}")

# decomposed_circuit.draw(output='mpl', style='bw', fold=50)

Depth of decomposed partitioned circuit: 316


We now optimise the node assignments using the recursive multilevel partitioning FM algorithm.

In [21]:
from disqco.parti.FM.multilevel_FM import MLFM_recursive
import numpy as np
from disqco.parti.FM.FM_main import run_FM

assignment_list, cost_list, _ = MLFM_recursive(
    graph,
    assignment,
    qpu_info,
    limit = num_qubits,
    log = True)


final_cost = min(cost_list)
final_assignment = assignment_list[np.argmin(cost_list)]

# if num_qubits <= 32:    
#     fig = draw_graph_tikz(H=graph,assignment=final_assignment,qpu_info=qpu_info)
#     display(fig)

Number of layers: 159
Number of layers: 159
Number of layers: 159
Number of layers: 159
Number of layers: 159
Number of layers: 159
Number of layers: 159
Number of layers: 159
Initial cost: 48
All passes complete.
Final cost: 46
Best cost at level 0: 46
Initial cost: 46
All passes complete.
Final cost: 46
Best cost at level 1: 46
Initial cost: 46
All passes complete.
Final cost: 47
Best cost at level 2: 46
Initial cost: 46
All passes complete.
Final cost: 46
Best cost at level 3: 46
Initial cost: 46
All passes complete.
Final cost: 50
Best cost at level 4: 46
Initial cost: 46
All passes complete.
Final cost: 48
Best cost at level 5: 46
Initial cost: 46
All passes complete.
Final cost: 46
Best cost at level 6: 46
Initial cost: 46
All passes complete.
Final cost: 46
Best cost at level 7: 46
Initial cost: 46
All passes complete.
Final cost: 46
Best cost at level 8: 46


Now define a new extractor for with the optimised assignment. 

In [22]:


extractor_opt = PartitionedCircuitExtractor(graph = graph, 
                                            partition_assignment = final_assignment, 
                                            qpu_info = qpu_info, 
                                            comm_info=comm_info)

partitioned_circuit_opt = extractor_opt.extract_partitioned_circuit()


print(f"Depth of optimised partitioned circuit: {partitioned_circuit_opt.depth()}")

partitioned_circuit_opt_EPR = transpile(partitioned_circuit_opt, basis_gates = ['cp', 'u', 'EPR'])

if 'EPR' in partitioned_circuit_opt_EPR.count_ops():
    EPR_count_opt = partitioned_circuit_opt_EPR.count_ops()['EPR']
else:
    EPR_count_opt = 0

print(f"EPR count in optimised partitioned circuit: {EPR_count_opt}")




Processing layer 0
Processing layer 1
Processing group gate {'type': 'group', 'root': 0, 'time': 1, 'sub-gates': [{'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 5], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 1}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 5], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 3}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 6], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 4}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 6], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 6}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 7], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 7}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 7], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 9}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 8], 'qregs': ['q', 'q'], 'params': [3.141592653589793], 'time': 10}, {'type': 'two-qubit', 'name': 'cp', 'qargs': [0, 8], 'qregs': ['q'

In [23]:
decomposed_circuit_opt = transpile(partitioned_circuit_opt, basis_gates = ['cp', 'u', 'EPR'])
print(f"Depth of decomposed partitioned circuit: {decomposed_circuit_opt.depth()}")

def get_wire_order(qc):
    """
    Build a valid wire_order from segments such as registers.
    Each segment must be an iterable of Bit objects.
    """


    reg_dict = {i : [] for i in range(num_partitions)}
    reg_list = []
    for reg in qc.qregs:
        QPU = int(reg.name[1])
        reg_dict[QPU].append(reg)
        
    for  i in range(num_partitions):
        for reg in reg_dict[i]:
            reg_list.append(reg)

    for creg in qc.cregs:
        reg_list.append(creg)
    
    bits = [bit for segment in reg_list for bit in segment]
    # if not creg_bundle:
    #     bits += qc.clbits  # show the remaining classical bits, if desired
    # if use_ints:
    idx = {b: i for i, b in enumerate(qc.qubits + qc.clbits)}
    return [idx[b] for b in bits]



# decomposed_circuit_opt.draw(output='mpl', style='bw', fold=50)



wo = get_wire_order(decomposed_circuit_opt)

print(wo)

# print(reg_dict)  
# # for creg in partitioned_circuit_opt.cregs:
# #     reg_dict[creg.name] = creg
# wire_order = []
# for i in range(num_partitions):
#     for reg in reg_dict[i]:
#         for qubit in reg:
#             print(qubit)
#             wire_order.append(qubit)

# print(wire_order)


partitioned_circuit_opt.draw(output='mpl', wire_order=wo, style='bw', fold=50)



Depth of decomposed partitioned circuit: 300
[0, 1, 2, 3, 4, 5, 6, 7, 33, 37, 40, 43, 46, 49, 52, 8, 9, 10, 11, 12, 13, 14, 15, 34, 16, 17, 18, 19, 20, 21, 22, 23, 35, 38, 41, 44, 47, 50, 53, 55, 57, 59, 24, 25, 26, 27, 28, 29, 30, 31, 32, 36, 39, 42, 45, 48, 51, 54, 56, 58, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94]


The depth of the resulting circuit should significantly lower than the unoptimised variant, though of course still much larger than the un-partitioned circuit. Some additional overhead is unavoidable.

## Validation

We would like to validate the output given by the partitioned circuit, which we can do using qiskits sampler class.

First we need to add measurements to the original, unpartitioned circuit.

In [24]:
from disqco.circuit_extraction.verification import run_sampler, plot, get_fidelity

circuit.measure_all()

data_circuit = run_sampler(circuit, shots=100000)
plot(data_circuit)



Too many qubits
No data to plot


In [25]:
# data_partitioned_circuit = run_sampler(basic_partitioned_circuit, shots=100000)
# plot(data_partitioned_circuit)


In [26]:
# data_partitioned_circuit_optimised = run_sampler(partitioned_circuit_opt, shots=100000)
# plot(data_partitioned_circuit_optimised)

In [27]:
# fidelity = get_fidelity(data_circuit, data_partitioned_circuit, shots=100000)

# print(f"Fidelity between original and unoptimised partitioned circuit: {fidelity}")

In [28]:
# fidelity = get_fidelity(data_circuit, data_partitioned_circuit_optimised, shots=100000)

# print(f"Fidelity between original and optimised partitioned circuit: {fidelity}")